In [1]:
import xml.etree.ElementTree as ET
import json
from os import walk
import os
import shutil
import urllib.request as request
from contextlib import closing

In [8]:
root = ET.parse('pubmed20n0001.xml').getroot()

In [9]:
res = []

for child in root:
    medlinecitation = child.find('MedlineCitation')
    PMID = medlinecitation.find('PMID').text
    
    article = medlinecitation.find('Article')
    articletitle = article.find('ArticleTitle').text
    
    abstract = article.find('Abstract')
    
    meshheadinglist = medlinecitation.find('MeshHeadingList')
    mesh = []
    for meshheading in meshheadinglist.findall('MeshHeading'):
        for i in meshheading:
            mesh.append(i.text)
    chemicallist = medlinecitation.find('ChemicalList')
    chemicaladd = []
    if not chemicallist:
        continue
    for chemical in chemicallist.findall('Chemical'):
        chemicaladd.append(chemical.find('NameOfSubstance').text)
    if abstract:
        abstracttext = abstract.find('AbstractText').text
        res.append([PMID,articletitle,abstracttext,mesh,chemicaladd])
    else:
        res.append([PMID,articletitle,'N/A',mesh,chemicaladd])

In [10]:
res

[['1',
  'Formate assay in body fluids: application in methanol poisoning.',
  'N/A',
  ['Aldehyde Oxidoreductases',
   'metabolism',
   'Animals',
   'Body Fluids',
   'analysis',
   'Carbon Dioxide',
   'blood',
   'Formates',
   'blood',
   'poisoning',
   'Haplorhini',
   'Humans',
   'Hydrogen-Ion Concentration',
   'Kinetics',
   'Methanol',
   'blood',
   'Methods',
   'Pseudomonas',
   'enzymology'],
  ['Formates', 'Carbon Dioxide', 'Aldehyde Oxidoreductases', 'Methanol']],
 ['2',
  'Delineation of the intimate details of the backbone conformation of pyridine nucleotide coenzymes in aqueous solution.',
  'N/A',
  ['Fourier Analysis',
   'Magnetic Resonance Spectroscopy',
   'Models, Molecular',
   'Molecular Conformation',
   'NAD',
   'analogs & derivatives',
   'NADP',
   'Structure-Activity Relationship',
   'Temperature'],
  ['NAD', 'NADP']],
 ['3',
  'Metal substitutions incarbonic anhydrase: a halide ion probe study.',
  'N/A',
  ['Animals',
   'Binding Sites',
   'Cadmiu

In [28]:
#clinical trials

In [2]:
folders = os.listdir('clinical_trials.0/')
files = []
for i in folders:
    if 'NCT' in i:
        for j in os.listdir('clinical_trials.0/'+i):
            files.append('clinical_trials.0/'+i+'/'+j)


In [30]:
files

['clinical_trials.0/NCT0093xxxx/NCT00932399.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00937222.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00935623.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00939757.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00932789.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00937183.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00931294.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00932945.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00935025.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00932776.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00937430.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00938717.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00935233.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00930410.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00938925.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00935597.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00932763.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00931242.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00931281.xml',
 'clinical_trials.0/NCT0093xxxx/NCT00937196.xml',


In [31]:
files[0]

'clinical_trials.0/NCT0093xxxx/NCT00932399.xml'

In [10]:
# 改brief_summary,detailed_description里的rationale,objective以及去掉\n
overallres = dict()
for file in files:
    #print(file)
    root = ET.parse(file).getroot()
    nct_id = root.find('id_info').find('nct_id').text
    brief_title = root.find('brief_title').text
    official_title = root.find('official_title')
    if official_title:
        official_title = official_title.text
    else:
        official_title = ''
    brief_summary = root.find('brief_summary')
    if brief_summary:
        brief_summary = brief_summary.find('textblock').text
        brief_summary = brief_summary.replace('rationale','')
        brief_summary = brief_summary.replace('objective','')
        brief_summary = brief_summary.replace('\n','')
    else:
        brief_summary = ''
    detailed_description = root.find('detailed_description')
    if detailed_description:
        detailed_description = detailed_description.find('textblock').text
        detailed_description = detailed_description.replace('rationale','')
        detailed_description = detailed_description.replace('objective','')
        detailed_description = detailed_description.replace('\n','')
    else:
        detailed_description = ''
    study_type = root.find('study_type').text
    intervention = root.find('intervention')
    if intervention:
        intervention_type = intervention.find('intervention_type').text
    else:
        intervention_type = ''
    eligibility = root.find('eligibility')
    if eligibility:
        criteria = eligibility.find('criteria')
        if criteria:
            criteria = root.find('eligibility').find('criteria').find('textblock').text
            if 'Inclusion Criteria' in criteria and 'Exclusion Criteria' in criteria:
                temp = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')
                if len(temp)==2:
                    inclusion_criteria = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')[0]
                    exclusion_criteria = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')[1]
                    inclusion_criteria = inclusion_criteria.replace('rationale','')
                    inclusion_criteria = inclusion_criteria.replace('objective','')
                    inclusion_criteria = inclusion_criteria.replace('\n','')
                    exclusion_criteria = exclusion_criteria.replace('rationale','')
                    exclusion_criteria = exclusion_criteria.replace('objective','')
                    exclusion_criteria = exclusion_criteria.replace('\n','')
                else:
                    inclusion_criteria = ''
                    exclusion_criteria = ''
            else:
                inclusion_criteria = ''
                exclusion_criteria = ''
        else:
            inclusion_criteria = ''
            exclusion_criteria = ''
        
        healthy_volunteers = root.find('eligibility').find('healthy_volunteers')
        if healthy_volunteers:
            healthy_volunteers = healthy_volunteers.text
        else:
            healthy_volunteers = ''
    else:
        inclusion_criteria = ''
        exclusion_criteria = ''
        healthy_volunteers = ''
    keywordlist = []
    keywords = root.findall('keyword')
    for i in keywords:
        keywordlist.append(i.text)
    condition_browse = root.find('condition_browse')
    if condition_browse:
        meshterms = condition_browse.findall('mesh_term')
    else:
        meshterms = []
    mesh_term_list = []
    for i in meshterms:
        mesh_term_list.append(i.text)
    res = dict()
    #res['nct_id'] = nct_id
    res['brief_title'] = brief_title
    res['official_title'] = official_title
    res['brief_summary'] = brief_summary
    res['detailed_description'] = detailed_description
    res['study_type'] = study_type
    res['intervention_type'] = intervention_type
    res['inclusion_criteria'] = inclusion_criteria
    res['exclusion_criteria'] = exclusion_criteria
    res['healthy_volunteers'] = healthy_volunteers
    res['keyword'] = keywordlist
    res['meshterm'] = mesh_term_list
    overallres[nct_id]=res

In [11]:
overallres

{'NCT00932399': {'brief_title': 'Longitudinal Study of Weight Change Following Lower Limb Amputation',
  'official_title': '',
  'brief_summary': '      The purpose of this study is to assess weight change in a population of Veterans with      amputations. Little is known about the how weight changes following an amputation. It is      widely believed that many patients experience weight gain following amputation. This study      aims to identify magnitude of weight changes following amputation and determine      characteristics associated with weight gain. Information on weight change trajectories would      be useful to better understand long-term health consequences associated with amputation and      to design and target interventions to encourage weight maintenance and general health      promotion for groups at high risk of weight gain.    ',
  'detailed_description': '',
  'study_type': 'Observational',
  'intervention_type': '',
  'inclusion_criteria': ':        "Exposed" cohor

In [90]:
root = ET.parse('clinical_trials.0/NCT0044xxxx/NCT00442754.xml').getroot()
nct_id = root.find('id_info').find('nct_id').text
brief_title = root.find('brief_title').text
official_title = root.find('official_title').text
brief_summary = root.find('brief_summary')
if brief_summary:
    brief_summary = brief_summary.find('textblock').text
else:
    brief_summary = ''
detailed_description = root.find('detailed_description')
if detailed_description:
    detailed_description = detailed_description.find('textblock').text
else:
    detailed_description = ''
study_type = root.find('study_type').text
intervention_type = root.find('intervention').find('intervention_type').text
criteria = root.find('eligibility').find('criteria').find('textblock').text
inclusion_criteria = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')[0]
exclusion_criteria = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')[1]
healthy_volunteers = root.find('eligibility').find('healthy_volunteers').text
keywordlist = []
keywords = root.findall('keyword')
for i in keywords:
    keywordlist.append(i.text)
condition_browse = root.find('condition_browse')
meshterms = condition_browse.findall('mesh_term')
mesh_term_list = []
for i in meshterms:
    mesh_term_list.append(i.text)
res = dict()
res['nct_id'] = nct_id
res['brief_title'] = brief_title
res['official_title'] = official_title
res['brief_summary'] = brief_summary
res['detailed_description'] = detailed_description
res['study_type'] = study_type
res['intervention_type'] = intervention_type
res['inclusion_criteria'] = inclusion_criteria
res['exclusion_criteria'] = exclusion_criteria
res['healthy_volunteers'] = healthy_volunteers
res['keyword'] = keywordlist
res['meshterm'] = mesh_term_list

AttributeError: 'NoneType' object has no attribute 'find'

In [91]:
list(root.find('eligibility'))

[<Element 'gender' at 0x10a384a48>,
 <Element 'minimum_age' at 0x10a3849f8>,
 <Element 'maximum_age' at 0x10a3849a8>,
 <Element 'healthy_volunteers' at 0x10a3846d8>]

In [73]:
list(criteria)

[<Element 'criteria' at 0x1092b9a48>,
 <Element 'gender' at 0x1092b9c78>,
 <Element 'minimum_age' at 0x1092b9cc8>,
 <Element 'maximum_age' at 0x1092b9688>,
 <Element 'healthy_volunteers' at 0x1092b9278>]

In [10]:
with closing(request.urlopen('ftp://ftp.ncbi.nlm.nih.gov/pubmed/baseline/pubmed20n0001.xml.gz')) as r:
    with open('temp.xml.gz', 'wb') as f:
        shutil.copyfileobj(r, f)

In [5]:
urllib.urlretrieve('ftp://ftp.ncbi.nlm.nih.gov/pubmed/baseline/README.txt', 'file')

AttributeError: module 'urllib' has no attribute 'urlretrieve'

In [14]:
for i in range (1,10):
    with closing(request.urlopen('ftp://ftp.ncbi.nlm.nih.gov/pubmed/baseline/pubmed20n' + "{0:0=4d}".format(i) + '.xml.gz')) as r:
        with open("{0:0=4d}".format(i) + '.xml.gz', 'wb') as f:
            shutil.copyfileobj(r, f)

In [39]:
for i in range (10,50):
    with closing(request.urlopen('ftp://ftp.ncbi.nlm.nih.gov/pubmed/baseline/pubmed20n' + "{0:0=4d}".format(i) + '.xml.gz')) as r:
        with open("{0:0=4d}".format(i) + '.xml.gz', 'wb') as f:
            shutil.copyfileobj(r, f)

In [73]:
dic = {}

In [74]:
def pubmed_preprocess (file_name):
    root = ET.parse(file_name).getroot()

    res = []

    for child in root:
        medlinecitation = child.find('MedlineCitation')
        PMID = medlinecitation.find('PMID').text
    
        article = medlinecitation.find('Article')
        if article:
            temp = article.find('ArticleTitle').itertext()
            articletitle = ''
            for i in temp:
                articletitle += i
        else:
            articletitle = ''
    
        abstract = article.find('Abstract')
        meshheadinglist = medlinecitation.find('MeshHeadingList')
        mesh = []
        if meshheadinglist:
            for meshheading in meshheadinglist.findall('MeshHeading'):
                for i in meshheading:
                    mesh.append(i.text.lower())
        chemicallist = medlinecitation.find('ChemicalList')
        chemicaladd = []
        if chemicallist:
            for chemical in chemicallist.findall('Chemical'):
                chemicaladd.append(chemical.find('NameOfSubstance').text.lower())
        #print(abstract)
        if abstract:
            temp = abstract.find('AbstractText').itertext()
            abstracttext = ''
            for i in temp:
                abstracttext += i
            #print(abstracttext)
            #abstracttext = abstract.find('AbstractText').text.lower()
            res.append([PMID,articletitle,abstracttext,mesh,chemicaladd])



    for line in res:
        dic[line[0]] = {'title': line[1], 'abstract': line[2], 'mesh': line[3], 'chemical': line[4]}

In [75]:
pubmed_preprocess('pubmed19n0970.xml')

<Element 'Abstract' at 0x114f556d8>
<Element 'Abstract' at 0x1261fe1d8>
<Element 'Abstract' at 0x112c56688>
<Element 'Abstract' at 0x165408ae8>
<Element 'Abstract' at 0x169f6eef8>
<Element 'Abstract' at 0x112845908>
<Element 'Abstract' at 0x1c78eee58>
<Element 'Abstract' at 0x1eb20c228>
<Element 'Abstract' at 0x17ed6b0e8>
<Element 'Abstract' at 0x17ed7b0e8>
<Element 'Abstract' at 0x1db8b3908>
<Element 'Abstract' at 0x1db897098>
<Element 'Abstract' at 0x1db8dac78>
<Element 'Abstract' at 0x127bbbae8>
<Element 'Abstract' at 0x127b945e8>
<Element 'Abstract' at 0x169e1aa48>
<Element 'Abstract' at 0x169e1c2c8>
<Element 'Abstract' at 0x17e9a84f8>
<Element 'Abstract' at 0x169e24a98>
<Element 'Abstract' at 0x17e70d0e8>
<Element 'Abstract' at 0x169bd8ae8>
<Element 'Abstract' at 0x1c98ec5e8>
<Element 'Abstract' at 0x1c9911048>
<Element 'Abstract' at 0x1131e47c8>
<Element 'Abstract' at 0x17e9f77c8>
<Element 'Abstract' at 0x17e9d8d68>
<Element 'Abstract' at 0x17ea08f98>
<Element 'Abstract' at 0x17e

None
None
None
None
None
None
<Element 'Abstract' at 0x119d20408>
<Element 'Abstract' at 0x119d25f48>
<Element 'Abstract' at 0x119d35ea8>
<Element 'Abstract' at 0x119d46548>
<Element 'Abstract' at 0x119d52ea8>
<Element 'Abstract' at 0x119d66138>
<Element 'Abstract' at 0x119d70188>
<Element 'Abstract' at 0x119d80048>
None
<Element 'Abstract' at 0x119da45e8>
<Element 'Abstract' at 0x119db4d68>
<Element 'Abstract' at 0x119dbd5e8>
<Element 'Abstract' at 0x119dc8138>
<Element 'Abstract' at 0x119dcdbd8>
<Element 'Abstract' at 0x119dd7ae8>
<Element 'Abstract' at 0x119de26d8>
<Element 'Abstract' at 0x119dec048>
<Element 'Abstract' at 0x119df7048>
<Element 'Abstract' at 0x119dfbbd8>
None
None
<Element 'Abstract' at 0x119e0ecc8>
<Element 'Abstract' at 0x119e174a8>
<Element 'Abstract' at 0x119e21368>
<Element 'Abstract' at 0x119e2b4f8>
<Element 'Abstract' at 0x119e37868>
<Element 'Abstract' at 0x119e42a48>
<Element 'Abstract' at 0x119e4c958>
<Element 'Abstract' at 0x119e5b098>
<Element 'Abstract'

None
<Element 'Abstract' at 0x1268bd818>
<Element 'Abstract' at 0x1268c8db8>
<Element 'Abstract' at 0x1268dd4a8>
<Element 'Abstract' at 0x1268e9e08>
<Element 'Abstract' at 0x1268f90e8>
<Element 'Abstract' at 0x1269099a8>
<Element 'Abstract' at 0x126919548>
<Element 'Abstract' at 0x126922ae8>
<Element 'Abstract' at 0x1269364a8>
<Element 'Abstract' at 0x126941f48>
<Element 'Abstract' at 0x126957d68>
<Element 'Abstract' at 0x126968048>
<Element 'Abstract' at 0x12696d688>
<Element 'Abstract' at 0x12697dd18>
<Element 'Abstract' at 0x126987b88>
<Element 'Abstract' at 0x126991ea8>
<Element 'Abstract' at 0x1269a2b38>
<Element 'Abstract' at 0x1269b2408>
None
<Element 'Abstract' at 0x1269cb1d8>
None
<Element 'Abstract' at 0x1269e1188>
<Element 'Abstract' at 0x1269e5f98>
<Element 'Abstract' at 0x1269eeb38>
<Element 'Abstract' at 0x1269ff228>
<Element 'Abstract' at 0x126a0e278>
<Element 'Abstract' at 0x126a17868>
<Element 'Abstract' at 0x126a26908>
<Element 'Abstract' at 0x126a30f98>
<Element 'Abs

<Element 'Abstract' at 0x12e731638>
<Element 'Abstract' at 0x12e73a9a8>
<Element 'Abstract' at 0x12e744868>
<Element 'Abstract' at 0x12e7509a8>
<Element 'Abstract' at 0x12e759a98>
<Element 'Abstract' at 0x12e762bd8>
<Element 'Abstract' at 0x12e774098>
<Element 'Abstract' at 0x12e77fa98>
<Element 'Abstract' at 0x12e78de08>
None
<Element 'Abstract' at 0x12e7a6598>
None
<Element 'Abstract' at 0x12e7b6e58>
<Element 'Abstract' at 0x12e7c0a48>
<Element 'Abstract' at 0x12e7d3c78>
<Element 'Abstract' at 0x12e7e6cc8>
<Element 'Abstract' at 0x12e7fa098>
<Element 'Abstract' at 0x12e80e5e8>
<Element 'Abstract' at 0x12e8170e8>
<Element 'Abstract' at 0x12e821188>
<Element 'Abstract' at 0x12e82b9a8>
<Element 'Abstract' at 0x12e83c548>
<Element 'Abstract' at 0x12e8464a8>
<Element 'Abstract' at 0x12e850e58>
<Element 'Abstract' at 0x12e85ff48>
<Element 'Abstract' at 0x12e873818>
<Element 'Abstract' at 0x12e883138>
<Element 'Abstract' at 0x12e88a228>
<Element 'Abstract' at 0x12e8957c8>
<Element 'Abstract

<Element 'Abstract' at 0x1393b8cc8>
<Element 'Abstract' at 0x1393c3e08>
<Element 'Abstract' at 0x1393cccc8>
<Element 'Abstract' at 0x1393d7818>
<Element 'Abstract' at 0x1393e1f98>
<Element 'Abstract' at 0x1393eb8b8>
<Element 'Abstract' at 0x1393f52c8>
<Element 'Abstract' at 0x1393fbe58>
<Element 'Abstract' at 0x13940a598>
<Element 'Abstract' at 0x139415598>
<Element 'Abstract' at 0x13941aef8>
<Element 'Abstract' at 0x1394239a8>
<Element 'Abstract' at 0x13942e8b8>
<Element 'Abstract' at 0x13943d188>
<Element 'Abstract' at 0x139442e08>
<Element 'Abstract' at 0x139452458>
<Element 'Abstract' at 0x13945c598>
None
<Element 'Abstract' at 0x13946b818>
<Element 'Abstract' at 0x1394745e8>
<Element 'Abstract' at 0x13947fd68>
<Element 'Abstract' at 0x1394889a8>
<Element 'Abstract' at 0x139491ae8>
<Element 'Abstract' at 0x1394a1cc8>
None
<Element 'Abstract' at 0x1394b6408>
<Element 'Abstract' at 0x1394c0868>
<Element 'Abstract' at 0x1394d1368>
<Element 'Abstract' at 0x1394db1d8>
<Element 'Abstract

...

<Element 'Abstract' at 0x1544a1f48>
<Element 'Abstract' at 0x1544b1a48>
<Element 'Abstract' at 0x1544bcb38>
<Element 'Abstract' at 0x1544cb188>
<Element 'Abstract' at 0x1544d9818>
<Element 'Abstract' at 0x1544ebcc8>
<Element 'Abstract' at 0x1544fa1d8>
<Element 'Abstract' at 0x154503138>
<Element 'Abstract' at 0x15450f688>
None
<Element 'Abstract' at 0x154527188>
<Element 'Abstract' at 0x154533638>
<Element 'Abstract' at 0x15453cef8>
<Element 'Abstract' at 0x15454b688>
<Element 'Abstract' at 0x15455ca98>
<Element 'Abstract' at 0x154568d68>
<Element 'Abstract' at 0x1545728b8>
None
<Element 'Abstract' at 0x154586d68>
<Element 'Abstract' at 0x1545942c8>
<Element 'Abstract' at 0x15459eb38>
<Element 'Abstract' at 0x1545adef8>
<Element 'Abstract' at 0x1545b7ea8>
<Element 'Abstract' at 0x1545c1638>
<Element 'Abstract' at 0x1545cc9a8>
<Element 'Abstract' at 0x1545d7368>
<Element 'Abstract' at 0x1545e7048>
<Element 'Abstract' at 0x1545eb958>
<Element 'Abstract' at 0x1545f4b88>
<Element 'Abstract

<Element 'Abstract' at 0x15d12fa98>
<Element 'Abstract' at 0x15d13e9f8>
<Element 'Abstract' at 0x15d14c548>
<Element 'Abstract' at 0x15d156728>
<Element 'Abstract' at 0x15d1609a8>
<Element 'Abstract' at 0x15d1704f8>
<Element 'Abstract' at 0x15d17e7c8>
<Element 'Abstract' at 0x15d18cb38>
<Element 'Abstract' at 0x15d19b7c8>
<Element 'Abstract' at 0x15d1a7bd8>
<Element 'Abstract' at 0x15d1b6548>
<Element 'Abstract' at 0x15d1c0ea8>
<Element 'Abstract' at 0x15d1cf4f8>
<Element 'Abstract' at 0x15d1dd048>
<Element 'Abstract' at 0x15d1e7778>
<Element 'Abstract' at 0x15d1f9f48>
<Element 'Abstract' at 0x15d202cc8>
<Element 'Abstract' at 0x15d20cef8>
<Element 'Abstract' at 0x15d21bb38>
<Element 'Abstract' at 0x15d22a318>
<Element 'Abstract' at 0x15d237818>
<Element 'Abstract' at 0x15d245098>
<Element 'Abstract' at 0x15d2504a8>
<Element 'Abstract' at 0x15d25cb38>
<Element 'Abstract' at 0x15d26c2c8>
<Element 'Abstract' at 0x15d2774f8>
<Element 'Abstract' at 0x15d286a98>
<Element 'Abstract' at 0x15d

<Element 'Abstract' at 0x167165ae8>
<Element 'Abstract' at 0x167176a48>
<Element 'Abstract' at 0x1671850e8>
<Element 'Abstract' at 0x167190598>
<Element 'Abstract' at 0x1671a6318>
None
<Element 'Abstract' at 0x1671c4228>
<Element 'Abstract' at 0x1671cf228>
<Element 'Abstract' at 0x1671d9728>
<Element 'Abstract' at 0x1671e4db8>
<Element 'Abstract' at 0x1671f2408>
<Element 'Abstract' at 0x167201188>
<Element 'Abstract' at 0x16720c3b8>
<Element 'Abstract' at 0x1672204a8>
<Element 'Abstract' at 0x1672394a8>
<Element 'Abstract' at 0x167248598>
<Element 'Abstract' at 0x167258e08>
<Element 'Abstract' at 0x167261ef8>
<Element 'Abstract' at 0x167276e58>
None
<Element 'Abstract' at 0x16728e098>
<Element 'Abstract' at 0x16729c2c8>
<Element 'Abstract' at 0x1672ae728>
<Element 'Abstract' at 0x1672bb098>
<Element 'Abstract' at 0x1672d7138>
<Element 'Abstract' at 0x1672e80e8>
<Element 'Abstract' at 0x1672f65e8>
<Element 'Abstract' at 0x1673000e8>
<Element 'Abstract' at 0x167305a48>
<Element 'Abstract

<Element 'Abstract' at 0x1cf8842c8>
<Element 'Abstract' at 0x1cf88ad68>
<Element 'Abstract' at 0x1cf893d18>
<Element 'Abstract' at 0x1cf8ba958>
<Element 'Abstract' at 0x1cf8d8e08>
<Element 'Abstract' at 0x1cf8f57c8>
<Element 'Abstract' at 0x1cf907bd8>
<Element 'Abstract' at 0x1cf932ea8>
<Element 'Abstract' at 0x1cf95e318>
<Element 'Abstract' at 0x1cf96ab88>
<Element 'Abstract' at 0x1cf98ff98>
<Element 'Abstract' at 0x1cf9b8e08>
<Element 'Abstract' at 0x1cf9cba98>
<Element 'Abstract' at 0x1cf9d54f8>
<Element 'Abstract' at 0x1cf9dbea8>
<Element 'Abstract' at 0x1cfa04818>
<Element 'Abstract' at 0x1cfa0e2c8>
<Element 'Abstract' at 0x1cfa12c78>
<Element 'Abstract' at 0x1cfa21908>
<Element 'Abstract' at 0x1cfa2e458>
<Element 'Abstract' at 0x1cfa37a48>
<Element 'Abstract' at 0x1cfa41368>
<Element 'Abstract' at 0x1cfa47958>
<Element 'Abstract' at 0x1cfa53cc8>
<Element 'Abstract' at 0x1cfa5c318>
<Element 'Abstract' at 0x1cfa65f98>
<Element 'Abstract' at 0x1cfa6e688>
<Element 'Abstract' at 0x1cf

<Element 'Abstract' at 0x1db240a48>
<Element 'Abstract' at 0x1db249408>
<Element 'Abstract' at 0x1db24de58>
<Element 'Abstract' at 0x1db257908>
<Element 'Abstract' at 0x1db2602c8>
<Element 'Abstract' at 0x1db266bd8>
<Element 'Abstract' at 0x1db270548>
<Element 'Abstract' at 0x1db279138>
<Element 'Abstract' at 0x1db27eb88>
<Element 'Abstract' at 0x1db2894f8>
<Element 'Abstract' at 0x1db2920e8>
<Element 'Abstract' at 0x1db297b38>
<Element 'Abstract' at 0x1db2a2368>
<Element 'Abstract' at 0x1db2a7db8>
<Element 'Abstract' at 0x1db2b6408>
<Element 'Abstract' at 0x1db2bbd18>
<Element 'Abstract' at 0x1db2c6688>
<Element 'Abstract' at 0x1db2cbe58>
<Element 'Abstract' at 0x1db2d4908>
<Element 'Abstract' at 0x1db2de188>
<Element 'Abstract' at 0x1db2e4958>
<Element 'Abstract' at 0x1db2ee408>
<Element 'Abstract' at 0x1db2f2e58>
<Element 'Abstract' at 0x1db2fa908>
<Element 'Abstract' at 0x1db305638>
<Element 'Abstract' at 0x1db30f0e8>
<Element 'Abstract' at 0x1db319098>
<Element 'Abstract' at 0x1db

In [77]:
dic['30456869']

{'title': 'The importance of early diagnosis of Mycobacterium abscessus complex in patients with cystic fibrosis.',
 'abstract': 'Mycobacterium abscessus complex can cause severe lung infections and has proven to be a serious threat to patients with cystic fibrosis and a challenge for clinicians due to difficulties in timely diagnosis and complex multidrug treatment regimes. Mycobacterial culture is the gold standard for diagnosis, but in most cystic fibrosis centers it is performed less frequently than culture for other pathogens. Consensus today recommends just one annual mycobacterial culture for asymptomatic patients with cystic fibrosis, a strategy likely to lead to diagnostic delays. Postponement of diagnosis might be the deciding factor in whether an early colonization turns into chronic infection. This review highlights the latest developments in knowledge about the pathogenicity and clinical consequences of M.\xa0abscessus complex pulmonary disease, addressing the central them

In [11]:
root = ET.parse('pubmed19n0970.xml').getroot()

In [55]:
for child in root:
    medlinecitation = child.find('MedlineCitation')
    article = medlinecitation.find('Article')
    if article:
        temp = article.find('ArticleTitle').itertext()
        curstr = ''
        for i in temp:
            curstr += i
        print(curstr)
        #articletitle = article.find('ArticleTitle').text.lower()

Role of Downregulation and Phosphorylation of Cofilin in Polarized Growth, MpkA Activation and Stress Response of Aspergillus fumigatus.
Corrigendum: Collection and Curation of Transcriptional Regulatory Interactions in Aspergillus nidulans and Neurospora crassa Reveal Structural and Evolutionary Features of the Regulatory Networks.
Swine Enteric Colibacillosis in Spain: Pathogenic Potential of mcr-1 ST10 and ST131 E. coli Isolates.
Enhanced Interferon-β Response Contributes to Eosinophilic Chronic Rhinosinusitis.
A Distinct Esophageal mRNA Pattern Identifies Eosinophilic Esophagitis Patients With Food Impactions.
The Vacuolar Pathway in Macrophages Plays a Major Role in Antigen Cross-Presentation Induced by the Pore-Forming Protein Sticholysin II Encapsulated Into Liposomes.
CD9 Controls Integrin α5β1-Mediated Cell Adhesion by Modulating Its Association With the Metalloproteinase ADAM17.
Tumor-Derived Microvesicles Enhance Cross-Processing Ability of Clinical Grade Dendritic Cells.
mi

Stratification by quality induced selection bias in a meta-analysis of clinical trials.
Generalizability of findings from Randomized Controlled Trials is limited in the Leading General Medical Journals.
Randomised trial seeking to induce the Hawthorne effect found no evidence for any effect on self-reported alcohol consumption online.
"An Error in An Old Paper Illustrates the Need for Data/Code Archives".
The azole fungicide tebuconazole affects human CYP1A1 and CYP1A2 expression by an aryl hydrocarbon receptor-dependent pathway.
RIFM fragrance ingredient safety assessment, octahydro-4,7-methano-1H-indenemethyl formate, CAS Registry Number 68039-78-1.
Uncertainty surrounding the mechanism and safety of the post-harvest fungicide fludioxonil.
Plumbagin from a tropical pitcher plant (Nepenthes alata Blanco) induces apoptotic cell death via a p53-dependent pathway in MCF-7 human breast cancer cells.
Comparative transcriptome analyses of venom glands from three scorpionfishes.
RIFM fragran

"Freshman effect" in gynecologic surgery at a teaching hospital.
The participation rate of migrant women in gestational diabetes screening in Austria: a retrospective analysis of 3293 births.
Accuracy and efficacy of embryo transfer based on the previous measurement of cervical length and total uterine length.
Amyloid β1-42-Induced Rapid Zn2+ Influx into Dentate Granule Cells Attenuates Maintained LTP Followed by Retrograde Amnesia.
Local Application of Autologous Platelet-Rich Fibrin Patch (PRF-P) Suppresses Regulatory T Cell Recruitment in a Murine Glioma Model.
Differential Role of Hypothalamic AMPKα Isoforms in Fish: an Evolutive Perspective.
Detecting medical prescriptions suspected of fraud using an unsupervised data mining algorithm.
Laparoscopy reduces iatrogenic splenic injuries during colorectal surgery.
Perforated sigmoid diverticulitis: Hartmann's procedure or resection with primary anastomosis.
Unpacking multi-trophic herbivore-grass-endophyte interactions: feedbacks acros

Black spruce assimilates nitrate in boreal winter.
Quantifying the Impact of Excluding Insecticide Classes From Cotton Integrated Pest Management Programs in the U.S. Mid-South.
The Association Between Acupuncture Training and Opioid Prescribing Practices.
Analysis of a Military Parachutist Injury - A Retrospective Review of Over 37,000 Landings‡.
COXPRESdb v7: a gene coexpression database for 11 animal species supported by 23 coexpression platforms for technical evaluation and evolutionary inference.
heZEB2, a master regulator of the epithelial-mesenchymal transition, mediates trophoblast differentiation.
Whole-genome multilocus sequence typing of closely related broiler chicken meat origin Campylobacter jejuni ST-5 isolates.
Letter from the Executive Director November/December 2018.
Comparative genetic characterization of third-generation cephalosporin-resistant Escherichia coli isolated from a layer operation system in Korea.
A novel approach to candidemia? The potential role of che

Distinct activity-gated pathways mediate attraction and aversion to CO2 in Drosophila.
U-Pb-dated flowstones restrict South African early hominin record to dry climate phases.
[Programa de detección del alelo APOE-E4 en adultos mayores mexicanos con deterioro cognitivo].
Amphioxus functional genomics and the origins of vertebrate gene regulation.
Recent History of Aedes aegypti: Vector Genomics and Epidemiology Records.
Temperature-Driven Biodiversity Change: Disentangling Space and Time.
Poetry as a Creative Practice to Enhance Engagement and Learning in Conservation Science.
Corrigendum: Rethinking Living Fossils.
Fruit Morphology and Anatomy of the Spondioid Anacardiaceae.
DOES UNDOCUMENTED IMMIGRATION INCREASE VIOLENT CRIME?
Mortality and life expectancy forecast for (comparatively) high mortality countries.
An analysis of the complementary stereoselective alkylations of imidazolidinone derivatives toward α-quaternary proline-based amino amides.
A macrolactonization-based strategy 

...

A pilot evaluation of incorporating "opt-out" naloxone dispensing within a chain community pharmacy.
Effects of the Intravenous Calcimimetic Etelcalcetide on Bone Turnover and Serum Fibroblast Growth Factor 23: Post Hoc Analysis of an Open-Label Study.
Pharmacovigilance: Challenges in Getting From Here to There.
Familial hyperuricaemic nephropathy: New mutation in uromodulin gen.
Predicting treatment response to antidepressant medication using early changes in emotional processing.
Reply.
The contribution of women to pancreatic knowledge.
The evolving role of the chaperone in medicine-protection and training: A plastic surgery perspective.
Feeding Induces Left Atrial Compression and Impedes Cardiac Filling in Patients With Large Hiatal Hernia.
Treatment Experiences, Information Needs, Pain and Quality of Life in Men with Metastatic Castrate-resistant Prostate Cancer: Results from the EXTREQOL Study.
Establishment and 12-month progress of the New Zealand Motor Neurone Disease Registry.


Erratum.
Ecophysiological strategy switch through development in heteroblastic species of mediterranean ecosystems - an example in the African Restionaceae.
Pan-Asian adapted ESMO Clinical Practice Guidelines for the management of patients with metastatic oesophageal cancer; a JSMO-ESMO initiative endorsed by CSCO, KSMO, MOS, SSO and TOS.
Widespread Incorrect Implementation of the Hoffmann Method, the Correct Approach, and Modern Alternatives.
Title: Pembrolizumab Monotherapy for Previously Untreated, PD-L1-Positive, Metastatic Triple-Negative Breast Cancer: Cohort B of the Phase 2 KEYNOTE-086 Study.
Biological background of the genomic variations of cf-DNA in healthy individuals.
Risk Set Matching to Assess the Impact of Hospital-Acquired Bloodstream Infections.
Pembrolizumab Monotherapy for Previously Treated Metastatic Triple-Negative Breast Cancer: Cohort A of the Phase 2 KEYNOTE-086 Study.
Exaggeration of PFS by blinded, independent, central review (BICR).
Discordant Partial Throm

Avoiding common pitfalls in machine learning omic data science.
Highly mechanosensitive ion channels from graphene-embedded crown ethers.
From EMUC18.
Discovery of the first genome-wide significant risk loci for attention deficit/hyperactivity disorder.
A comparison of the Macintosh laryngoscope, McGrath video laryngoscope, and Pentax Airway Scope in paediatric nasotracheal intubation.
Understanding flow dynamics, viability and metastatic potency of cervical cancer (HeLa) cells through constricted microchannel.
Escherichia coli "Marionette" strains with 12 highly optimized small-molecule sensors.
Exploiting the vicinal disubstituent effect on the diastereoselective synthesis of γ and δ lactones.
DNA flower-encapsulated horseradish peroxidase with enhanced biocatalytic activity synthesized by an isothermal one-pot method based on rolling circle amplification.
Shape dependence of thermodynamics of adsorption on nanoparticles: a theoretical and experimental study.
Terahertz phase jumps fo

Autologous Blood Patch Injection versus Hydrogel Plug in CT-guided Lung Biopsy: A Prospective Randomized Trial.
Interreader Variability of Dynamic Contrast-enhanced MRI of Recurrent Glioblastoma: The Multicenter ACRIN 6677/RTOG 0625 Study.
Detection of Colorectal Hepatic Metastases Is Superior at Standard Radiation Dose CT versus Reduced Dose CT.
Shear-Wave Elastography of Benign versus Malignant Musculoskeletal Soft-Tissue Masses: Comparison with Conventional US and MRI.
The RSNA Pediatric Bone Age Machine Learning Challenge.
Fluorine 18-FDG PET/CT and Diffusion-weighted MRI for Malignant versus Benign Pulmonary Lesions: A Meta-Analysis.
Building Simulation Exercise Capacity in Latin America to Manage Public Health Emergencies.
US Global Health Security Investments Improve Capacities for Infectious Disease Emergencies.
Building Global Health Security Capacity: The Role for Implementation Science.
Building Laboratory-Based Arbovirus Sentinel Surveillance Capacity During an Ongoing Deng

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [50]:
temp = root[0][0][2][1].itertext()

In [51]:
for i in temp:
    print(i)

Role of Downregulation and Phosphorylation of Cofilin in Polarized Growth, MpkA Activation and Stress Response of 
Aspergillus fumigatus
.


In [69]:
root[0][0][2][4][0]

<Element 'AbstractText' at 0x169f88318>

In [70]:
temp = root[0][0][2][4][0].itertext()
abstracttext = ''
for i in temp:
    abstracttext += i
print(abstracttext)

Aspergillus fumigatus causes most of aspergillosis in clinic and comprehensive function analysis of its key protein would promote anti-aspergillosis. In a previous study, we speculated actin depolymerizing factor cofilin might be essential for A. fumigatus viability and found its overexpression upregulated oxidative response and cell wall polysaccharide synthesis of this pathogen. Here, we constructed a conditional cofilin mutant to determine the essential role of cofilin. And the role of cofilin downregulation and phosphorylation in A. fumigatus was further analyzed. Cofilin was required for the polarized growth and heat sensitivity of A. fumigatus. Downregulation of cofilin caused hyphal cytoplasmic leakage, increased the sensitivity of A. fumigatus to sodium dodecyl sulfonate but not to calcofluor white and Congo Red and farnesol, and enhanced the basal phosphorylation level of MpkA, suggesting that cofilin affected the cell wall integrity (CWI) signaling. Downregulation of cofilin 

In [40]:
root[0][0][2].tail

'\n      '

In [39]:
type(root[0][0][2])

xml.etree.ElementTree.Element

In [43]:
with open('output_test.json', 'w') as output:
    json.dump(dic, output, indent=4)

In [42]:
len(dic.keys())

452197

In [45]:
overallres = dict()

In [46]:
def clinical_preprocess (folder_name):
    folders = os.listdir(folder_name)
    files = []
    for i in folders:
        if 'NCT' in i:
            for j in os.listdir(folder_name+i):
                files.append(folder_name+i+'/'+j)


    
    for file in files:
        #print(file)
        root = ET.parse(file).getroot()
        nct_id = root.find('id_info').find('nct_id').text
        brief_title = root.find('brief_title').text
        official_title = root.find('official_title')
        if official_title:
            official_title = official_title.text
        else:
            official_title = ''
        brief_summary = root.find('brief_summary')
        if brief_summary:
            brief_summary = brief_summary.find('textblock').text
            brief_summary = brief_summary.replace('rationale','')
            brief_summary = brief_summary.replace('objective','')
            brief_summary = brief_summary.replace('\n','')
        else:
            brief_summary = ''
        detailed_description = root.find('detailed_description')
        if detailed_description:
            detailed_description = detailed_description.find('textblock').text
            detailed_description = detailed_description.replace('rationale','')
            detailed_description = detailed_description.replace('objective','')
            detailed_description = detailed_description.replace('\n','')
        else:
            detailed_description = ''
        study_type = root.find('study_type').text
        intervention = root.find('intervention')
        if intervention:
            intervention_type = intervention.find('intervention_type').text
        else:
            intervention_type = ''
        eligibility = root.find('eligibility')
        if eligibility:
            criteria = eligibility.find('criteria')
            if criteria:
                criteria = root.find('eligibility').find('criteria').find('textblock').text
                if 'Inclusion Criteria' in criteria and 'Exclusion Criteria' in criteria:
                    temp = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')
                    if len(temp)==2:
                        inclusion_criteria = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')[0]
                        exclusion_criteria = criteria.split('Inclusion Criteria')[1].split('Exclusion Criteria')[1]
                        inclusion_criteria = inclusion_criteria.replace('rationale','')
                        inclusion_criteria = inclusion_criteria.replace('objective','')
                        inclusion_criteria = inclusion_criteria.replace('\n','')
                        exclusion_criteria = exclusion_criteria.replace('rationale','')
                        exclusion_criteria = exclusion_criteria.replace('objective','')
                        exclusion_criteria = exclusion_criteria.replace('\n','')
                    else:
                        inclusion_criteria = ''
                        exclusion_criteria = ''
                else:
                    inclusion_criteria = ''
                    exclusion_criteria = ''
            else:
                inclusion_criteria = ''
                exclusion_criteria = ''

            healthy_volunteers = root.find('eligibility').find('healthy_volunteers')
            if healthy_volunteers:
                healthy_volunteers = healthy_volunteers.text
            else:
                healthy_volunteers = ''
        else:
            inclusion_criteria = ''
            exclusion_criteria = ''
            healthy_volunteers = ''
        keywordlist = []
        keywords = root.findall('keyword')
        for i in keywords:
            keywordlist.append(i.text)
        condition_browse = root.find('condition_browse')
        if condition_browse:
            meshterms = condition_browse.findall('mesh_term')
        else:
            meshterms = []
        mesh_term_list = []
        for i in meshterms:
            mesh_term_list.append(i.text)
        res = dict()
        #res['nct_id'] = nct_id
        res['brief_title'] = brief_title
        res['official_title'] = official_title
        res['brief_summary'] = brief_summary
        res['detailed_description'] = detailed_description
        res['study_type'] = study_type
        res['intervention_type'] = intervention_type
        res['inclusion_criteria'] = inclusion_criteria
        res['exclusion_criteria'] = exclusion_criteria
        res['healthy_volunteers'] = healthy_volunteers
        res['keyword'] = keywordlist
        res['meshterm'] = mesh_term_list
        overallres[nct_id]=res


In [47]:
clinical_preprocess('clinical_trials.0/')

In [49]:
clinical_preprocess('clinical_trials.1/')

In [50]:
clinical_preprocess('clinical_trials.2/')

In [51]:
clinical_preprocess('clinical_trials.3/')

In [52]:
with open('output_test_clinical_together.json','w') as output:
    json.dump(overallres,output,indent = 4)

In [48]:
len(overallres.keys())

79759